In [35]:
import pandas as pd
import numpy as np

In [39]:
file = 'dashboard_data.csv'

In [41]:
price_df_hour = pd.read_csv(file, sep=',', decimal=',')

price_df_hour['Time'] = pd.to_datetime(price_df_hour['Time'])
price_df_hour['Nord Pool Lietuva'] = pd.to_numeric(price_df_hour['Nord Pool Lietuva'], errors='coerce').fillna(0).astype(np.int64)
price_df_hour = price_df_hour.set_index('Time')

In [42]:
price_df_hour.head(5)

Nord Pool Lietuva
Time                                  
2015-01-01 00:00:00                 28
2015-01-01 01:00:00                 30
2015-01-01 02:00:00                 30
2015-01-01 03:00:00                 30
2015-01-01 04:00:00                 30

In [43]:
price_df_day = price_df_hour.resample('D').mean()

In [48]:
import statistics

class DataAggregator:

    def mean(self, array):
        if len(array) == 0:
            return 0
        return sum(array) / len(array)

    def sum(self, array):
        return sum(array)

    def min(self, array):
        return min(array)

    def max(self, array):
        return max(array)

    def median(self, array):
        return statistics.median(array)

    def work_hours_mean(self, array):
        arr = array[7:16]
        return self.mean(arr)

    def night_hours_mean(self, array):
        arr = (array[0:6]).append(array[18:23])
        return self.mean(arr)

    def max_values_average(self, array):
        count = 5
        copy = array
        arr = []
        print(array)
        for i in range(0, count):
            mv = self.max(copy)
            arr.append(mv)

            copy = copy.drop(mv)
        return self.mean(arr)

In [49]:
agg = DataAggregator()
price_df_day = price_df_hour.resample('D').apply(agg.mean)
price_df_day.head(5)

Nord Pool Lietuva
Time                         
2015-01-01          33.250000
2015-01-02          26.125000
2015-01-03          28.458333
2015-01-04          29.250000
2015-01-05          41.875000

In [51]:
%store price_df_day

Stored 'price_df_day' (DataFrame)


In [52]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [53]:
price_data_hour = go.Scatter(x=price_df_hour.index,
                         y=price_df_hour['Nord Pool Lietuva'])
price_data_day = go.Scatter(x=price_df_day.index,
                         y=price_df_day['Nord Pool Lietuva'])

In [54]:
layout = go.Layout(title='Energy Plot', xaxis=dict(title='Date'),
                   yaxis=dict(title='(EUR/MWh)'))

In [55]:
fig = go.Figure(data=[price_data_hour, price_data_day], layout=layout)
fig.show()